# Введение

Это курсовая работа 3 курса бакалавриата.  В первой части анализируется реестр зелёных насаждений с целью выявления закономерностей разпределения деревьев в Москве. Во второй части анализируются мониторинговые данные с датчиков Tree Talkers

In [1]:
import geopandas as gpd
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
# библиотека для визуализации
%matplotlib widget
import matplotlib.pyplot as plt
from libpysal.weights import Queen
from esda.moran import Moran
import plotly.express as px
import plotly.graph_objects as go

# Часть 1. АИС Реестр зелёных насаждений г. Москвы

В АркГИС почистила шейпфайл от  кустов *class: bush*  
и оставила только деревья *class: tree*

In [2]:
# Загрузка shapefile с точками
# тут всегда вылетает кернел
points = gpd.read_file('dpioos_green_stands_utm37n/dpioos_green_stands_utm37n.shp')

In [6]:
lands = gpd.read_file('data_n37/data_n37/dpioos_green_landing_utm37n.shp')
lands.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 104400 entries, 0 to 104399
Data columns (total 9 columns):
 #   Column      Non-Null Count   Dtype   
---  ------      --------------   -----   
 0   objectid    104400 non-null  int64   
 1   class       104400 non-null  object  
 2   species_ru  104332 non-null  object  
 3   d_trunk_m   34929 non-null   float64 
 4   height_m    104382 non-null  float64 
 5   species_l   0 non-null       object  
 6   d_canopy_m  0 non-null       object  
 7   source      104400 non-null  object  
 8   geometry    104400 non-null  geometry
dtypes: float64(2), geometry(1), int64(1), object(5)
memory usage: 7.2+ MB


In [7]:
lands.describe()

objectid     d_trunk_m       height_m
count  104400.000000  34929.000000  104382.000000
mean    52592.326102      0.082319       2.801792
std     30263.963849      2.364299     136.068879
min         1.000000      0.000000       0.040000
25%     26581.750000      0.020000       1.000000
50%     52681.500000      0.040000       1.400000
75%     78781.250000      0.080000       2.000000
max    104881.000000    441.120000   43952.000000

In [8]:
lands.species_ru.unique()

array(['Береза повислая (бородавчатая, обыкновенная)',
       'Липа мелколистная', None, 'Клен ясенелистный',
       'Яблоня обыкновенная', 'Рябина обыкновенная', 'Клен остролистный',
       'Тополь бальзамический', 'Ясень', 'Вяз гладкий',
       'Вишня обыкновенная', 'Липа европейская (обыкновенная)',
       'Яблоня сибирская', 'Ясень обыкновенный', 'Слива обыкновенная',
       'Туя западная', 'Вяз шершавый', 'Боярышник',
       'Боярышник вееролистный (колючий, обыкновенный, сглаженный)',
       'Лавровишня лекарственная', 'Слива домашняя', 'Ива белая', 'Вяз',
       'Яблоня домашняя', 'Тополь дрожащий (осина)', 'Ива пятитычинковая',
       'Ясень пенсильванский', 'Каштан конский обыкновенный',
       'Черемуха обыкновенная', 'Туя восточная (Биота)',
       'Облепиха крушиновидная (крушиновая, обыкновенная)', 'Ива козья',
       'Ель колючая ф.голубая', 'Клен приречный (гиннала)',
       'Боярышник кроваво-красный (сибирский)', 'Спирея японская',
       'Ель обыкновенная (европейская

In [4]:
points.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 5100660 entries, 0 to 5100659
Data columns (total 10 columns):
 #   Column      Dtype   
---  ------      -----   
 0   objectid    int64   
 1   species_ru  object  
 2   species_l   object  
 3   height_m    float64 
 4   d_trunk_m   float64 
 5   d_canopy_m  object  
 6   class       object  
 7   source      object  
 8   adm_region  object  
 9   geometry    geometry
dtypes: float64(2), geometry(1), int64(1), object(6)
memory usage: 389.1+ MB


In [5]:
points.head()

objectid                      species_ru species_l  height_m  d_trunk_m  \
0   2920027                  Клен татарский      None       1.3       0.02   
1   2920707              Вишня обыкновенная      None       2.0       0.02   
2   2920695  Ель обыкновенная (европейская)      None       2.0       0.06   
3   2920301     Каштан конский обыкновенный      None       2.0       0.04   
4   2920838           Тополь бальзамический      None       2.0       0.06   

  d_canopy_m class         source                adm_region  \
0       None  Tree  DPIOOS Moscow             район Савёлки   
1       None  Tree  DPIOOS Moscow           Можайский район   
2       None  Tree  DPIOOS Moscow           Можайский район   
3       None  Tree  DPIOOS Moscow              район Щукино   
4       None  Tree  DPIOOS Moscow  район Нагатино-Садовники   

                         geometry  
0  POINT (389917.199 6207402.099)  
1  POINT (399607.241 6175167.105)  
2  POINT (399683.528 6175531.449)  
3  POINT (405022.406 6184562.092)  
4  POINT (413473.774 6169387.397)

## Часть 1.1 исследуем как расположены в Москве виды деревьев, на которых висят TreeTalkers

NB! Это не значит что на каждом дереве из этой выборки висит Три Токер  
Это значит что на выбранных видах как минимум один Три Токер в МСК висит

In [5]:
# Список видов
species = [
    'Липа мелколистная', 
    'Клен остролистный', 
    'Тополь дрожащий (осина)', 
    'Дуб черешчатый', 
    'Сосна обыкновенная', 
    'Береза белая', 
    'Береза повислая (бородавчатая, обыкновенная)', 
    'Ель обыкновенная (европейская)', 
    'Ель колючая', 
    'Клен серебристый (канадский, сахаристый)'
]

# Фильтрация точек по наличию видов из списка
points_filtered = points[points['species_ru'].isin(species)]

# Присвоение латинских названий видов в столбец species_l
for i, row in points_filtered.iterrows():
    species_ru = row['species_ru']
    species_l = {
        'Липа мелколистная': 'Tilia cordata',
        'Клен остролистный': 'Acer platanoides',
        'Тополь дрожащий (осина)': 'Populus tremula',
        'Дуб черешчатый': 'Quercus robur',
        'Сосна обыкновенная': 'Pinus silvestris',
        'Береза белая': 'Betula alba',
        'Береза повислая (бородавчатая, обыкновенная)': 'Betula pendula',
        'Ель обыкновенная (европейская)': 'Picea abies',
        'Ель колючая': 'Picea pungens',
        'Клен серебристый (канадский, сахаристый)': 'Acer saccharinum'
    }.get(species_ru)
    points_filtered.at[i, 'species_l'] = species_l

# Сохранение отфильтрованных точек в новый shapefile
# points_filtered.to_file('moscow_points_filtered.shp')

In [6]:
# points_filtered = gpd.read_file('moscow_points_filtered.shp')
# прекрасный файл - всего-то 1,8 млн точек 
points_filtered

objectid                                    species_ru  \
2         2920695                Ель обыкновенная (европейская)   
8         2922304                                   Ель колючая   
11        2923399                             Клен остролистный   
13        2925638                             Липа мелколистная   
30        2930856                            Сосна обыкновенная   
...           ...                                           ...   
5100653   1607513  Береза повислая (бородавчатая, обыкновенная)   
5100654   1687450                             Клен остролистный   
5100657   2007542                             Клен остролистный   
5100658   2080143                             Клен остролистный   
5100659   2080144  Береза повислая (бородавчатая, обыкновенная)   

                species_l  height_m  d_trunk_m d_canopy_m class  \
2             Picea abies       2.0       0.06       None  Tree   
8           Picea pungens       2.0       0.04       None  Tree   
11       Acer platanoides       2.0       0.02       None  Tree   
13          Tilia cordata       2.0       0.04       None  Tree   
30       Pinus silvestris       2.0       0.02       None  Tree   
...                   ...       ...        ...        ...   ...   
5100653    Betula pendula      17.0       0.30       None  Tree   
5100654  Acer platanoides      18.0       0.32       None  Tree   
5100657  Acer platanoides       7.0       0.10       None  Tree   
5100658  Acer platanoides      14.0       0.10       None  Tree   
5100659    Betula pendula      16.0       0.32       None  Tree   

                source              adm_region                        geometry  
2        DPIOOS Moscow         Можайский район  POINT (399683.528 6175531.449)  
8        DPIOOS Moscow          район Строгино  POINT (400472.190 6185385.176)  
11       DPIOOS Moscow            район Щукино  POINT (404492.216 6186233.988)  
13       DPIOOS Moscow    район Филёвский Парк  POINT (402870.360 6177918.957)  
30       DPIOOS Moscow  городской округ Троицк  POINT (392947.167 6151616.394)  
...                ...                     ...                             ...  
5100653  DPIOOS Moscow         район Кузьминки  POINT (407580.550 6163724.088)  
5100654  DPIOOS Moscow         район Кузьминки  POINT (411505.338 6196434.131)  
5100657  DPIOOS Moscow         район Кузьминки  POINT (402639.190 6166723.136)  
5100658  DPIOOS Moscow         район Кузьминки  POINT (399036.663 6178837.848)  
5100659  DPIOOS Moscow         район Кузьминки  POINT (399897.766 6179573.653)  

[1799700 rows x 10 columns]

In [5]:
# чтобы больше никогда не загружать тот первый файл
# но тут кернел тоже может умереть :(
# Загрузим точечный shapefile Москвы
points_f = gpd.read_file('moscow_points_filtered.shp')
points_f.species_l.unique()

array(['Picea abies', 'Picea pungens', 'Acer platanoides',
       'Tilia cordata', 'Pinus silvestris', 'Betula pendula',
       'Populus tremula', 'Acer saccharinum', 'Quercus robur',
       'Betula alba'], dtype=object)

здесь надо почистить деревья по высотам и диаметру сначала:  
1) тем что невероятно высокие задать медиан

In [8]:
# Calculate the mean height for each species
mean_heights = points_f.groupby('species_l')['height_m'].median()

# Convert the result to a pandas DataFrame
result = pd.DataFrame({'species_l': mean_heights.index, 'mean_height': mean_heights.values})

# Print the result
print(result)

          species_l  mean_height
0  Acer platanoides         11.0
1  Acer saccharinum          8.0
2       Betula alba         10.0
3    Betula pendula         15.0
4       Picea abies          2.0
5     Picea pungens          5.0
6  Pinus silvestris          6.0
7   Populus tremula         11.0
8     Quercus robur         15.0
9     Tilia cordata         13.0


In [6]:
# create a dictionary of unique species_ru values and their counts
species_dict = dict(points_f['species_l'].value_counts())

In [16]:
import plotly.graph_objects as go

# сортируем значения в порядке убывания количества по видам
tt_species = dict(sorted(species_dict.items(), key=lambda x: x[1], reverse=True)[:])

# делаем списки для шкал
species = list(tt_species.keys())
counts = list(tt_species.values())

# Define custom colors for the bars
custom_colors = ['#FFB347'] * 3 + ['#636EFA'] * (len(species) - 3)

# Create a bar chart with custom colors
bar_trace = go.Bar(x=species, y=counts, marker=dict(color=custom_colors))

# Set up the layout with adjusted width, height, and font size
layout = go.Layout(
    title=dict(text='Виды, на которых висят TreeTalkers и их количество в Москве', font=dict(size=24)),
    xaxis=dict(title='Species', tickangle=45, title_font=dict(size=18), tickfont=dict(size=20)),
    yaxis=dict(title='Count', title_font=dict(size=18), tickfont=dict(size=14)),
    width=800,
    height=800
)

# Create the Figure and display it
fig = go.Figure(data=[bar_trace], layout=layout)
fig.show()


Тут уже наша первая мысль - хорошо бы вешать больше ТТ на деревья которых много, а не те, которых мало

### Лирическое отступление в QGIS

Дальше произошло некоторое перемещение в QGIS, потому что играться с кластерами было проще, быстрее и приятнее в ПО, чем в Python
1) Сгенерировала гексагональную сетку 250 м
2) Обрезала по границе МСК
3) Аггрегировала в каждый гексагон количество точек по 10 видам = получила 10 колонок с названием вида

NB! Сейчас в этом шейпфайле уже больше колонок, чем 10 потому что я аггрегировала туда топ 10 видов по всей москве с медианной высотой от 5 м

In [6]:
# Read hexagon data shapefile into a geodataframe
hexagon_data = gpd.read_file('hexagons.shp')
hexagon_data.head()

left        bottom          right           top  acer_plata  \
0  363250.0  6.142432e+06  363583.333489  6.142721e+06         0.0   
1  363250.0  6.142721e+06  363583.333489  6.143010e+06         0.0   
2  363250.0  6.143010e+06  363583.333489  6.143298e+06         0.0   
3  363250.0  6.143298e+06  363583.333489  6.143587e+06         2.0   
4  363250.0  6.143587e+06  363583.333489  6.143876e+06         0.0   

   acer_sacch  betula_alb  picea_abie  picea_pung  pinus_silv  ...  \
0         0.0         0.0         0.0         0.0         0.0  ...   
1         0.0         0.0         0.0         0.0         0.0  ...   
2         0.0         0.0         0.0         0.0         0.0  ...   
3         0.0         0.0         2.0         0.0         3.0  ...   
4         0.0         0.0         0.0         0.0         0.0  ...   

   tilia_cord  acer_negun  aesculus_h  betula_p_1  fraxinus_e  fraxinus_p  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         5.0         7.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   malus_dome  populus_ba  sorbus_auc  \
0         0.0         0.0         0.0   
1         0.0         0.0         0.0   
2         0.0         0.0         0.0   
3         0.0         0.0         0.0   
4         0.0         0.0         0.0   

                                            geometry  
0  POLYGON ((363250.000 6142576.715, 363333.333 6...  
1  POLYGON ((363250.000 6142865.391, 363333.333 6...  
2  POLYGON ((363250.000 6143154.066, 363333.333 6...  
3  POLYGON ((363250.000 6143442.741, 363333.333 6...  
4  POLYGON ((363250.000 6143731.417, 363333.333 6...  

[5 rows x 22 columns]

In [12]:
hexagon_data.columns

Index(['left', 'bottom', 'right', 'top', 'acer_plata', 'acer_sacch',
       'betula_alb', 'picea_abie', 'picea_pung', 'pinus_silv', 'populus_tr',
       'quercus_ro', 'tilia_cord', 'acer_negun', 'aesculus_h', 'betula_p_1',
       'fraxinus_e', 'fraxinus_p', 'malus_dome', 'populus_ba', 'sorbus_auc',
       'geometry'],
      dtype='object')

In [13]:
hexagon_data.describe()

left        bottom          right           top    acer_plata  \
count   35633.000000  3.563300e+04   35633.000000  3.563300e+04  35633.000000   
mean   397178.600277  6.159626e+06  397511.933766  6.159914e+06     16.115539   
std     16193.206395  2.152953e+04   16193.206395  2.152953e+04     47.259685   
min    363250.000000  6.119916e+06  363583.333489  6.120204e+06      0.000000   
25%    385000.010141  6.141711e+06  385333.343630  6.141999e+06      0.000000   
50%    397500.015969  6.159897e+06  397833.349458  6.160186e+06      0.000000   
75%    409500.021564  6.177073e+06  409833.355053  6.177362e+06      4.000000   
max    434000.032987  6.209549e+06  434333.366476  6.209838e+06   1430.000000   

         acer_sacch    betula_alb    picea_abie    picea_pung    pinus_silv  \
count  35633.000000  35633.000000  35633.000000  35633.000000  35633.000000   
mean       0.131451      0.025678      1.366795      0.522718      1.263267   
std        1.601038      0.853811      6.782173      2.810779     10.257248   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max      136.000000     82.000000    589.000000    113.000000   1109.000000   

       ...    quercus_ro    tilia_cord    acer_negun    aesculus_h  \
count  ...  35633.000000  35633.000000  35633.000000  35633.000000   
mean   ...      1.367384     15.294867     23.903825      2.223529   
std    ...      9.943870     46.496888     62.643163      6.751758   
min    ...      0.000000      0.000000      0.000000      0.000000   
25%    ...      0.000000      0.000000      0.000000      0.000000   
50%    ...      0.000000      0.000000      0.000000      0.000000   
75%    ...      0.000000      3.000000      6.000000      0.000000   
max    ...    736.000000   1468.000000   1099.000000    146.000000   

         betula_p_1    fraxinus_e    fraxinus_p    malus_dome    populus_ba  \
count  35633.000000  35633.000000  35633.000000  35633.000000  35633.000000   
mean      12.752196      6.508714      2.594982      2.526450      7.461174   
std       36.524398     20.244729     12.176377     10.841113     21.236271   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        4.000000      0.000000      0.000000      0.000000      1.000000   
max      847.000000    405.000000    317.000000    991.000000    344.000000   

         sorbus_auc  
count  35633.000000  
mean       5.249207  
std       15.687245  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        1.000000  
max      494.000000  

[8 rows x 21 columns]

Убираем полигоны, в которых нет видов с ТТ

In [7]:
hex_non_empty = hexagon_data.loc[
    (hexagon_data['acer_plata'] > 0) | 
    (hexagon_data['acer_sacch'] > 0) |
    (hexagon_data['betula_alb'] > 0) |
    (hexagon_data['picea_abie'] > 0) |
    (hexagon_data['picea_pung'] > 0) |
    (hexagon_data['pinus_silv'] > 0) |
    (hexagon_data['populus_tr'] > 0) |
    (hexagon_data['quercus_ro'] > 0) |
    (hexagon_data['tilia_cord'] > 0) |
    (hexagon_data['betula_p_1'] > 0)
]

In [15]:
hex_non_empty.describe()

left        bottom          right           top    acer_plata  \
count   12093.000000  1.209300e+04   12093.000000  1.209300e+04  12093.000000   
mean   409881.316706  6.175924e+06  410214.650195  6.176213e+06     47.485736   
std     10908.500093  1.361248e+04   10908.500093  1.361248e+04     71.356305   
min    363250.000000  6.119916e+06  363583.333489  6.120204e+06      0.000000   
25%    403500.018767  6.167691e+06  403833.352255  6.167980e+06      4.000000   
50%    410500.022030  6.176207e+06  410833.355519  6.176496e+06     23.000000   
75%    417500.025294  6.185301e+06  417833.358783  6.185589e+06     65.000000   
max    434000.032987  6.209405e+06  434333.366476  6.209694e+06   1430.000000   

         acer_sacch    betula_alb    picea_abie    picea_pung    pinus_silv  \
count  12093.000000  12093.000000  12093.000000  12093.000000  12093.000000   
mean       0.387332      0.075664      4.027371      1.540230      3.722319   
std        2.730262      1.464368     11.172637      4.659757     17.345775   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      1.000000      0.000000      0.000000   
75%        0.000000      0.000000      5.000000      1.000000      3.000000   
max      136.000000     82.000000    589.000000    113.000000   1109.000000   

       ...    quercus_ro    tilia_cord    acer_negun    aesculus_h  \
count  ...  12093.000000  12093.000000  12093.000000  12093.000000   
mean   ...      4.029108     45.067560     70.276772      6.536343   
std    ...     16.752617     70.914356     91.125311     10.255733   
min    ...      0.000000      0.000000      0.000000      0.000000   
25%    ...      0.000000      3.000000      5.000000      0.000000   
50%    ...      1.000000     22.000000     33.000000      2.000000   
75%    ...      3.000000     62.000000    106.000000      9.000000   
max    ...    736.000000   1468.000000   1099.000000    146.000000   

         betula_p_1    fraxinus_e    fraxinus_p    malus_dome    populus_ba  \
count  12093.000000  12093.000000  12093.000000  12093.000000  12093.000000   
mean      37.575374     19.138427      7.638717      7.435376     21.892086   
std       54.756089     31.066164     19.957610     17.601026     31.796851   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        3.000000      0.000000      0.000000      0.000000      1.000000   
50%       17.000000      6.000000      0.000000      2.000000      9.000000   
75%       50.000000     26.000000      6.000000      8.000000     30.000000   
max      847.000000    405.000000    317.000000    991.000000    344.000000   

         sorbus_auc  
count  12093.000000  
mean      15.448607  
std       23.820768  
min        0.000000  
25%        1.000000  
50%        7.000000  
75%       20.000000  
max      494.000000  

[8 rows x 21 columns]

In [16]:
# hex_non_empty.to_file('hex_non_empty.shp')

Идём в QGIS делать кластеризацию по k-means с 5 классами 

In [17]:
# Read hexagon data shapefile into a geodataframe
hex_non_empty = gpd.read_file('hex_non_empty.shp')
hex_non_empty.head()

left        bottom          right           top  acer_plata  \
0  363250.000000  6.143298e+06  363583.333489  6.143587e+06         2.0   
1  363250.000000  6.144453e+06  363583.333489  6.144742e+06         0.0   
2  363500.000117  6.143154e+06  363833.333605  6.143443e+06         0.0   
3  363500.000117  6.143443e+06  363833.333605  6.143731e+06         0.0   
4  363500.000117  6.144597e+06  363833.333605  6.144886e+06         0.0   

   acer_sacch  betula_alb  picea_abie  picea_pung  pinus_silv  ...  \
0         0.0         0.0         2.0         0.0         3.0  ...   
1         0.0         0.0         2.0         0.0         0.0  ...   
2         0.0         0.0         0.0         0.0         0.0  ...   
3         0.0         0.0         1.0         0.0         0.0  ...   
4         0.0         0.0         0.0         0.0         0.0  ...   

   acer_negun  aesculus_h  betula_p_1  fraxinus_e  fraxinus_p  malus_dome  \
0         0.0         5.0         7.0         0.0         0.0         0.0   
1         0.0         0.0         7.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         7.0         0.0         0.0         0.0   
4         0.0         0.0         1.0         0.0         0.0         0.0   

   populus_ba  sorbus_auc  class_5  \
0         0.0         0.0        1   
1         0.0         0.0        1   
2         0.0         0.0        1   
3         0.0         0.0        1   
4         0.0         0.0        1   

                                            geometry  
0  POLYGON ((363250.000 6143442.741, 363333.333 6...  
1  POLYGON ((363250.000 6144597.442, 363333.333 6...  
2  POLYGON ((363500.000 6143298.404, 363583.333 6...  
3  POLYGON ((363500.000 6143587.079, 363583.333 6...  
4  POLYGON ((363500.000 6144741.780, 363583.333 6...  

[5 rows x 23 columns]

### Пространственная автокорреляция
Делаем матрицу пространственных весов

In [18]:
# Create a spatial weights matrix
w = Queen.from_dataframe(hexagon_data)

/home/babykelp/anaconda3/lib/python3.9/site-packages/libpysal/weights/weights.py:172: UserWarning:

The weights matrix is not fully connected: 
 There are 5 disconnected components.



In [20]:
attr = ['acer_plata', 'tilia_cord', 'betula_p_1', 'populus_tr', 'quercus_ro', 'picea_abie', 'pinus_silv', 'picea_pung', 'acer_sacch', 'betula_alb']
for i in attr:
    # Calculate Moran I Index
    moran = Moran(hexagon_data[i], w)

    # Print Moran I Index and p-value
    print(f"Moran's I of {i}: ", moran.I)
    print(f"p-value of {i}: ", moran.p_sim)

Moran's I of acer_plata:  0.6183809675755726
p-value of acer_plata:  0.001
Moran's I of tilia_cord:  0.5798248559307824
p-value of tilia_cord:  0.001
Moran's I of betula_p_1:  0.5786478905297979
p-value of betula_p_1:  0.001
Moran's I of populus_tr:  0.17922656818433044
p-value of populus_tr:  0.001
Moran's I of quercus_ro:  0.3593433570894682
p-value of quercus_ro:  0.001
Moran's I of picea_abie:  0.25323582302449904
p-value of picea_abie:  0.001
Moran's I of pinus_silv:  0.1679384924563101
p-value of pinus_silv:  0.001
Moran's I of picea_pung:  0.27469945935845685
p-value of picea_pung:  0.001
Moran's I of acer_sacch:  0.2661174762888001
p-value of acer_sacch:  0.001
Moran's I of betula_alb:  0.18311173590914592
p-value of betula_alb:  0.001


### Кластеризация 

In [9]:
hex_non_empty = gpd.read_file('hex_non_empty.shp')

In [10]:
species_order = [
    'acer_plata', 
    'tilia_cord', 
    'betula_p_1', 
    'populus_tr', 
    'quercus_ro', 
    'picea_abie', 
    'pinus_silv', 
    'picea_pung', 
    'acer_sacch', 
    'betula_alb'
]

for i in range(len(hex_non_empty['class_5'].unique())):
    # Filter data by class
    class_data = hex_non_empty[hex_non_empty['class_5'] == i]
    
    # Melt data to create long format for Plotly
    melted_data = pd.melt(class_data, 
                          id_vars=['class_5'], 
                          value_vars= species_order,
                          var_name='species', 
                          value_name='value')
    # Change the order of melted_data using species_order
    melted_data['species'] = pd.Categorical(
        melted_data['species'], 
        categories=species_order, 
        ordered=True
    )

    melted_data = melted_data.sort_values(by='species')

    # Create box plot using Plotly
    fig = px.box(melted_data, x='species', y='value', color='species', 
                 title=f'Box Plot of Species by Class {i}')
    
    # Add line
    fig.add_trace(go.Scatter(
        x=species_order,
        y=melted_data.groupby('species')['value'].median(),
        mode='lines', 
        name='Median', 
        line=dict(color='red', width=3, dash='dot', shape='spline'))
    )

    fig.update_layout(height = 800, width = 800)
    fig.update_yaxes(range=[0, 600])
    fig.show()

В основном кластеризация произошла по количеству клёна остролистного, липы мелколистной и берёзы повислой.  
В последнем кластере выделяются некоторые различия в соотношении пары клён+липа и берёзы.